In [4]:
!pip install suffix-trees

twisted 18.7.0 requires PyHamcrest>=1.9.0, which is not installed.
You are using pip version 10.0.1, however version 19.0.1 is available.
You should consider upgrading via the 'python -m pip install --upgrade pip' command.


In [17]:
import psycopg2

try:
    conn = psycopg2.connect("dbname='db_alquran' user='postgres' host='localhost' password='12345'")
except:
    print("I am unable to connect to the database")

In [18]:
import psycopg2.extras

cur = conn.cursor(cursor_factory=psycopg2.extras.DictCursor)

In [19]:
cur.execute("""select id, surat, ayat, terjemah from alquran_indo order by surat, id, ayat""")

In [20]:
rows = cur.fetchall()

In [21]:
import pandas as pd
# import nltk
# from nltk.tokenize import RegexpTokenizer

In [22]:
rows

[[1,
  1,
  1,
  'Dengan menyebut nama Allah Yang Maha Pemurah lagi Maha Penyayang.'],
 [2, 1, 2, 'Segala puji bagi Allah, Tuhan semesta alam.'],
 [3, 1, 3, 'Maha Pemurah lagi Maha Penyayang.'],
 [4, 1, 4, 'Yang menguasai di Hari Pembalasan.'],
 [5,
  1,
  5,
  'Hanya Engkaulah yang kami sembah, dan hanya kepada Engkaulah kami meminta pertolongan.'],
 [6, 1, 6, 'Tunjukilah kami jalan yang lurus,'],
 [7,
  1,
  7,
  '(yaitu) Jalan orang-orang yang telah Engkau beri nikmat kepada mereka; bukan (jalan) mereka yang dimurkai dan bukan (pula jalan) mereka yang sesat.'],
 [8, 2, 1, 'Alif laam miim.'],
 [9,
  2,
  2,
  'Kitab (Al Quran) ini tidak ada keraguan padanya; petunjuk bagi mereka yang bertakwa,'],
 [10,
  2,
  3,
  '(yaitu) mereka yang beriman kepada yang ghaib, yang mendirikan shalat, dan menafkahkan sebahagian rezeki yang Kami anugerahkan kepada mereka.'],
 [11,
  2,
  4,
  'dan mereka yang beriman kepada Kitab (Al Quran) yang telah diturunkan kepadamu dan Kitab-kitab yang telah dit

In [23]:
rows_process = []
print("\nShow me the database:\n")
for row in rows:
    terjemah = row['terjemah']
    terjemah_low = terjemah.lower()
    terjemah_ganti_petik = terjemah_low.replace("'","").replace("\"","")
    terjemah_ganti_tanda = terjemah_ganti_petik.replace(",","").replace(".","").replace(":","").replace(";","")
    terjemah_ganti_kurung = terjemah_ganti_tanda.replace("(","").replace(")","")
    terjemah_token = terjemah_ganti_kurung.split(' ')
    terjemah_tanda = ['<'+ x + '>' for x in terjemah_token]
    terjemah_array = ' '.join(terjemah_tanda)
#     print(" ", row['id'])
#     print(" ", row['surat'])
#     print(" ", row['ayat'])
#     print(" ", terjemah_ganti_kurung)
    row_new = {
        'id': row['id'],
        'surat': row['surat'],
        'ayat': row['ayat'],
        'terjemah': terjemah,
        'terjemah_preprocess': terjemah_array
    }
    rows_process.append(row_new)
rows_process


Show me the database:



[{'id': 1,
  'surat': 1,
  'ayat': 1,
  'terjemah': 'Dengan menyebut nama Allah Yang Maha Pemurah lagi Maha Penyayang.',
  'terjemah_preprocess': '<dengan> <menyebut> <nama> <allah> <yang> <maha> <pemurah> <lagi> <maha> <penyayang>'},
 {'id': 2,
  'surat': 1,
  'ayat': 2,
  'terjemah': 'Segala puji bagi Allah, Tuhan semesta alam.',
  'terjemah_preprocess': '<segala> <puji> <bagi> <allah> <tuhan> <semesta> <alam>'},
 {'id': 3,
  'surat': 1,
  'ayat': 3,
  'terjemah': 'Maha Pemurah lagi Maha Penyayang.',
  'terjemah_preprocess': '<maha> <pemurah> <lagi> <maha> <penyayang>'},
 {'id': 4,
  'surat': 1,
  'ayat': 4,
  'terjemah': 'Yang menguasai di Hari Pembalasan.',
  'terjemah_preprocess': '<yang> <menguasai> <di> <hari> <pembalasan>'},
 {'id': 5,
  'surat': 1,
  'ayat': 5,
  'terjemah': 'Hanya Engkaulah yang kami sembah, dan hanya kepada Engkaulah kami meminta pertolongan.',
  'terjemah_preprocess': '<hanya> <engkaulah> <yang> <kami> <sembah> <dan> <hanya> <kepada> <engkaulah> <kami> <mem

In [8]:
# !pip install findspark


In [9]:
# import findspark 
# findspark.init()
# import pyspark.sql.functions as f
# my_udf = f.udf(my_func, StringType())

# rows['tokenized_terjemah'] = row.apply(lambda rows: nltk.word_tokenize(rows['terjemah']), axis=1)

In [ ]:
from suffix_trees import STree

list_hasil = []

print("\nShow me the database:\n")
for idx, row in enumerate(rows_process[0:6235]): #surat 1-5
    for idx, row2 in enumerate(rows_process[0:6235]):
        if row['id'] < row2['id']: # !=
            a = [row['terjemah_preprocess'], row2['terjemah_preprocess']]
            st = STree.STree(a)
            lcs = st.lcs()
            lcs_split = lcs.split(' ')
            filter_lcs = list(filter(lambda kata: kata.startswith("<") and kata.endswith(">"), lcs_split))
#             b = list(filter(lambda kata: len(kata) >= 2, lcs.split(' ')))
            jumlah_kata = len(filter_lcs)
#             print(jumlah_kata)
            if jumlah_kata >= 3:
#                 print(" ", idx, row['id'], " ", row2['id'])
#                 print(" ", idx, row['surat'], " ", row2['surat'])
#                 print(" ", idx, row['ayat'], " ", row2['ayat'])
#                 print(" ", idx, row['terjemah'], " ", row2['terjemah'])
#                 print(b)
                hilangkan_marker = [x[1:len(x)-1] for x in filter_lcs]
                terjemah_string = ' '.join(hilangkan_marker)
                print("Surat: ", row['surat'],"Surat Pembanding: ", row2['surat'], "Ayat: ", row['ayat'], "Ayat Pembanding: ", row2['ayat'], "LCS: ", terjemah_string)
                hasil = [row['surat'], row2['surat'], row['ayat'], row2['ayat'], jumlah_kata, terjemah_string]
                list_hasil.append(hasil)
        
print(len(list_hasil))


Show me the database:

Surat:  1 Surat Pembanding:  1 Ayat:  1 Ayat Pembanding:  3 LCS:  maha pemurah lagi maha penyayang
Surat:  1 Surat Pembanding:  2 Ayat:  1 Ayat Pembanding:  37 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  2 Ayat:  1 Ayat Pembanding:  54 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  2 Ayat:  1 Ayat Pembanding:  114 LCS:  menyebut nama allah
Surat:  1 Surat Pembanding:  2 Ayat:  1 Ayat Pembanding:  128 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  2 Ayat:  1 Ayat Pembanding:  143 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  2 Ayat:  1 Ayat Pembanding:  160 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  2 Ayat:  1 Ayat Pembanding:  163 LCS:  yang maha pemurah lagi maha penyayang
Surat:  1 Surat Pembanding:  2 Ayat:  1 Ayat Pembanding:  173 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  2 Ayat:  1 Ayat Pembanding:  182 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  2 Ayat:  1 Ayat Pembanding:  192 LCS:  l

Surat:  1 Surat Pembanding:  25 Ayat:  1 Ayat Pembanding:  26 LCS:  yang maha pemurah
Surat:  1 Surat Pembanding:  25 Ayat:  1 Ayat Pembanding:  59 LCS:  yang maha pemurah
Surat:  1 Surat Pembanding:  25 Ayat:  1 Ayat Pembanding:  70 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Ayat:  1 Ayat Pembanding:  5 LCS:  yang maha pemurah
Surat:  1 Surat Pembanding:  26 Ayat:  1 Ayat Pembanding:  9 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Ayat:  1 Ayat Pembanding:  68 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Ayat:  1 Ayat Pembanding:  104 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Ayat:  1 Ayat Pembanding:  122 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Ayat:  1 Ayat Pembanding:  140 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Ayat:  1 Ayat Pembanding:  159 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Ayat:  1 Ayat Pembanding:  175 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Aya

Surat:  1 Surat Pembanding:  7 Ayat:  2 Ayat Pembanding:  104 LCS:  tuhan semesta alam
Surat:  1 Surat Pembanding:  7 Ayat:  2 Ayat Pembanding:  121 LCS:  tuhan semesta alam
Surat:  1 Surat Pembanding:  10 Ayat:  2 Ayat Pembanding:  37 LCS:  tuhan semesta alam
Surat:  1 Surat Pembanding:  14 Ayat:  2 Ayat Pembanding:  39 LCS:  segala puji bagi allah
Surat:  1 Surat Pembanding:  17 Ayat:  2 Ayat Pembanding:  111 LCS:  segala puji bagi allah
Surat:  1 Surat Pembanding:  18 Ayat:  2 Ayat Pembanding:  1 LCS:  segala puji bagi allah
Surat:  1 Surat Pembanding:  23 Ayat:  2 Ayat Pembanding:  28 LCS:  segala puji bagi allah
Surat:  1 Surat Pembanding:  26 Ayat:  2 Ayat Pembanding:  16 LCS:  tuhan semesta alam
Surat:  1 Surat Pembanding:  26 Ayat:  2 Ayat Pembanding:  23 LCS:  tuhan semesta alam
Surat:  1 Surat Pembanding:  26 Ayat:  2 Ayat Pembanding:  47 LCS:  tuhan semesta alam
Surat:  1 Surat Pembanding:  26 Ayat:  2 Ayat Pembanding:  77 LCS:  tuhan semesta alam
Surat:  1 Surat Pembanding:

Surat:  1 Surat Pembanding:  21 Ayat:  3 Ayat Pembanding:  112 LCS:  maha pemurah lagi
Surat:  1 Surat Pembanding:  22 Ayat:  3 Ayat Pembanding:  65 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  24 Ayat:  3 Ayat Pembanding:  5 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  24 Ayat:  3 Ayat Pembanding:  22 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  24 Ayat:  3 Ayat Pembanding:  33 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  24 Ayat:  3 Ayat Pembanding:  62 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  25 Ayat:  3 Ayat Pembanding:  6 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  25 Ayat:  3 Ayat Pembanding:  70 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Ayat:  3 Ayat Pembanding:  9 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Ayat:  3 Ayat Pembanding:  68 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Ayat:  3 Ayat Pembanding:  104 LCS:  lagi maha penyayang
Surat:  1 Surat Pembanding:  26 Aya

Surat:  1 Surat Pembanding:  22 Ayat:  6 Ayat Pembanding:  54 LCS:  jalan yang lurus
Surat:  1 Surat Pembanding:  22 Ayat:  6 Ayat Pembanding:  67 LCS:  jalan yang lurus
Surat:  1 Surat Pembanding:  23 Ayat:  6 Ayat Pembanding:  73 LCS:  jalan yang lurus
Surat:  1 Surat Pembanding:  23 Ayat:  6 Ayat Pembanding:  74 LCS:  jalan yang lurus
Surat:  1 Surat Pembanding:  24 Ayat:  6 Ayat Pembanding:  46 LCS:  jalan yang lurus
Surat:  1 Surat Pembanding:  31 Ayat:  6 Ayat Pembanding:  32 LCS:  jalan yang lurus
Surat:  1 Surat Pembanding:  36 Ayat:  6 Ayat Pembanding:  4 LCS:  jalan yang lurus
Surat:  1 Surat Pembanding:  36 Ayat:  6 Ayat Pembanding:  61 LCS:  jalan yang lurus
Surat:  1 Surat Pembanding:  37 Ayat:  6 Ayat Pembanding:  118 LCS:  jalan yang lurus
Surat:  1 Surat Pembanding:  38 Ayat:  6 Ayat Pembanding:  22 LCS:  jalan yang lurus
Surat:  1 Surat Pembanding:  41 Ayat:  6 Ayat Pembanding:  6 LCS:  jalan yang lurus
Surat:  1 Surat Pembanding:  42 Ayat:  6 Ayat Pembanding:  52 LCS:

...

Surat:  2 Surat Pembanding:  3 Ayat:  203 Ayat Pembanding:  142 LCS:  bahwa kamu akan
Surat:  2 Surat Pembanding:  3 Ayat:  203 Ayat Pembanding:  179 LCS:  kepada allah dan
Surat:  2 Surat Pembanding:  3 Ayat:  203 Ayat Pembanding:  199 LCS:  kepada allah dan
Surat:  2 Surat Pembanding:  3 Ayat:  203 Ayat Pembanding:  200 LCS:  dan bertakwalah kepada allah
Surat:  2 Surat Pembanding:  4 Ayat:  203 Ayat Pembanding:  1 LCS:  dan bertakwalah kepada allah
Surat:  2 Surat Pembanding:  4 Ayat:  203 Ayat Pembanding:  6 LCS:  dan barangsiapa yang
Surat:  2 Surat Pembanding:  4 Ayat:  203 Ayat Pembanding:  9 LCS:  kepada allah dan
Surat:  2 Surat Pembanding:  4 Ayat:  203 Ayat Pembanding:  13 LCS:  kepada allah dan
Surat:  2 Surat Pembanding:  4 Ayat:  203 Ayat Pembanding:  14 LCS:  dan barangsiapa yang
Surat:  2 Surat Pembanding:  4 Ayat:  203 Ayat Pembanding:  59 LCS:  kepada allah dan
Surat:  2 Surat Pembanding:  4 Ayat:  203 Ayat Pembanding:  38 LCS:  kepada allah dan
Surat:  2 Surat Pemban

Surat:  2 Surat Pembanding:  13 Ayat:  203 Ayat Pembanding:  33 LCS:  dan barangsiapa yang
Surat:  2 Surat Pembanding:  14 Ayat:  203 Ayat Pembanding:  36 LCS:  dan barangsiapa yang
Surat:  2 Surat Pembanding:  15 Ayat:  203 Ayat Pembanding:  69 LCS:  dan bertakwalah kepada allah dan
Surat:  2 Surat Pembanding:  16 Ayat:  203 Ayat Pembanding:  30 LCS:  bagi orang yang bertakwa
Surat:  2 Surat Pembanding:  16 Ayat:  203 Ayat Pembanding:  35 LCS:  maka tidak ada
Surat:  2 Surat Pembanding:  16 Ayat:  203 Ayat Pembanding:  67 LCS:  bagi orang yang
Surat:  2 Surat Pembanding:  16 Ayat:  203 Ayat Pembanding:  120 LCS:  kepada allah dan
Surat:  2 Surat Pembanding:  16 Ayat:  203 Ayat Pembanding:  128 LCS:  yang bertakwa dan
Surat:  2 Surat Pembanding:  17 Ayat:  203 Ayat Pembanding:  15 LCS:  dan barangsiapa yang
Surat:  2 Surat Pembanding:  17 Ayat:  203 Ayat Pembanding:  18 LCS:  bagi orang yang
Surat:  2 Surat Pembanding:  17 Ayat:  203 Ayat Pembanding:  19 LCS:  dan barangsiapa yang
Sura

Surat:  2 Surat Pembanding:  45 Ayat:  203 Ayat Pembanding:  15 LCS:  dan barangsiapa yang
Surat:  2 Surat Pembanding:  46 Ayat:  203 Ayat Pembanding:  13 LCS:  maka tidak ada
Surat:  2 Surat Pembanding:  46 Ayat:  203 Ayat Pembanding:  31 LCS:  kepada allah dan
Surat:  2 Surat Pembanding:  47 Ayat:  203 Ayat Pembanding:  13 LCS:  maka tidak ada
Surat:  2 Surat Pembanding:  48 Ayat:  203 Ayat Pembanding:  9 LCS:  kepada allah dan
Surat:  2 Surat Pembanding:  48 Ayat:  203 Ayat Pembanding:  13 LCS:  dan barangsiapa yang
Surat:  2 Surat Pembanding:  48 Ayat:  203 Ayat Pembanding:  17 LCS:  dan barangsiapa yang
Surat:  2 Surat Pembanding:  48 Ayat:  203 Ayat Pembanding:  25 LCS:  bahwa kamu akan
Surat:  2 Surat Pembanding:  49 Ayat:  203 Ayat Pembanding:  1 LCS:  dan bertakwalah kepada allah
Surat:  2 Surat Pembanding:  49 Ayat:  203 Ayat Pembanding:  11 LCS:  dan barangsiapa yang
Surat:  2 Surat Pembanding:  49 Ayat:  203 Ayat Pembanding:  12 LCS:  dan bertakwalah kepada allah
Surat:  2 

Surat:  2 Surat Pembanding:  30 Ayat:  204 Ayat Pembanding:  46 LCS:  dan di antara
Surat:  2 Surat Pembanding:  31 Ayat:  204 Ayat Pembanding:  6 LCS:  dan di antara manusia ada orang yang
Surat:  2 Surat Pembanding:  31 Ayat:  204 Ayat Pembanding:  20 LCS:  dan di antara manusia ada
Surat:  2 Surat Pembanding:  33 Ayat:  204 Ayat Pembanding:  23 LCS:  dan di antara
Surat:  2 Surat Pembanding:  35 Ayat:  204 Ayat Pembanding:  27 LCS:  dan di antara
Surat:  2 Surat Pembanding:  35 Ayat:  204 Ayat Pembanding:  28 LCS:  di antara manusia
Surat:  2 Surat Pembanding:  35 Ayat:  204 Ayat Pembanding:  32 LCS:  dan di antara
Surat:  2 Surat Pembanding:  38 Ayat:  204 Ayat Pembanding:  26 LCS:  di antara manusia
Surat:  2 Surat Pembanding:  39 Ayat:  204 Ayat Pembanding:  56 LCS:  ada orang yang
Surat:  2 Surat Pembanding:  40 Ayat:  204 Ayat Pembanding:  78 LCS:  dan di antara
Surat:  2 Surat Pembanding:  41 Ayat:  204 Ayat Pembanding:  37 LCS:  dan di antara
Surat:  2 Surat Pembanding:  41 A

Surat:  2 Surat Pembanding:  9 Ayat:  206 Ayat Pembanding:  119 LCS:  bertakwalah kepada allah
Surat:  2 Surat Pembanding:  11 Ayat:  206 Ayat Pembanding:  78 LCS:  bertakwalah kepada allah


In [10]:
data_frame = pd.DataFrame(list_hasil, columns=['surat','surat_pembanding', 'ayat', 'ayat_pembanding', 'jumlah_kata', 'lcs'])
data_frame

surat  surat_pembanding  ayat  ayat_pembanding  jumlah_kata  \
0          1                 1     1                3            5   
1          1                 2     1               37            3   
2          1                 2     1               54            3   
3          1                 2     1              114            3   
4          1                 2     1              128            3   
5          1                 2     1              143            3   
6          1                 2     1              160            3   
7          1                 2     1              163            6   
8          1                 2     1              173            3   
9          1                 2     1              182            3   
10         1                 2     1              192            3   
11         1                 2     1              199            3   
12         1                 2     1              218            3   
13         1                 2     1              226            3   
14         1                 3     1               31            3   
15         1                 3     1               89            3   
16         1                 3     1              126            3   
17         1                 3     1              129            3   
18         1                 4     1               16            3   
19         1                 4     1               23            3   
20         1                 4     1               25            3   
21         1                 4     1               64            3   
22         1                 4     1               96            3   
23         1                 4     1              100            3   
24         1                 4     1              106            3   
25         1                 4     1              110            3   
26         1                 4     1              129            3   
27         1                 4     1              152            3   
28         1                 5     1                3            3   
29         1                 5     1               34            3   
...      ...               ...   ...              ...          ...   
20661      5                 5    94              105            4   
20662      5                 5    94              106            4   
20663      5                 5    95              101            6   
20664      5                 5    95              105            4   
20665      5                 5    95              106            7   
20666      5                 5    95              107            3   
20667      5                 5    96              100            3   
20668      5                 5    96              108            4   
20669      5                 5    96              112            3   
20670      5                 5    96              119            3   
20671      5                 5    97               98            5   
20672      5                 5    97               99            4   
20673      5                 5    97              116            4   
20674      5                 5    98              101            5   
20675      5                 5    99              116            3   
20676      5                 5   100              108            3   
20677      5                 5   100              112            3   
20678      5                 5   101              105            4   
20679      5                 5   101              106            4   
20680      5                 5   104              106            3   
20681      5                 5   105              106            4   
20682      5                 5   106              107            6   
20683      5                 5   106              112            3   
20684      5                 5   108              112            3   
20685      5                 5   109              116            3   
20686      5     

In [11]:
# from pandas import ExcelWriter

# writer = ExcelWriter('data_test2.xlsx')
# data_frame.to_excel(writer,'indo')
# writer.save()

In [12]:
data_frame.sort_values(by=['lcs', 'surat', 'ayat'])

surat  surat_pembanding  ayat  ayat_pembanding  jumlah_kata  \
16785      3                 5   192               72            3   
10497      2                 3   253               19            4   
6308       2                 2   173              182           10   
14939      3                 5   113               66            3   
109        2                 3     2                9            3   
7790       2                 3   200               75            3   
7794       2                 3   200              152            3   
7799       2                 3   200              199            3   
7803       2                 4   200               72            3   
7813       2                 2   201              204            3   
7814       2                 2   201              207            3   
7840       2                 3   201              152            3   
7844       2                 3   201              199            3   
7850       2                 4   201               72            3   
7961       2                 3   204               75            3   
7962       2                 3   204              152            3   
7963       2                 3   204              199            3   
7966       2                 4   204               72            3   
8030       2                 3   207               75            3   
8034       2                 3   207              152            3   
8039       2                 3   207              199            3   
8047       2                 4   207               72            3   
14128      3                 3    75              152            3   
14144      3                 4    75               72            3   
6038       2                 3   165              173            3   
6047       2                 4   165               33            3   
6053       2                 4   165               55            3   
6080       2                 5   165               22            3   
16430      3                 4   173               33            3   
16443      3                 5   173               22            3   
...      ...               ...   ...              ...          ...   
4705       2                 5   134               83            3   
4706       2                 5   134               93            3   
4972       2                 3   141              155            3   
4982       2                 4   141               81            3   
4995       2                 5   141               83            3   
4996       2                 5   141               93            3   
15935      3                 3   155              188            3   
15948      3                 4   155               81            3   
15974      3                 5   155               63            3   
15975      3                 5   155               64            3   
15977      3                 5   155               83            3   
15978      3                 5   155               93            3   
16717      3                 4   188               81            3   
16725      3                 5   188               83            3   
16726      3                 5   188               93            3   
18582      4                 5    81               63            3   
18584      4                 5    81               83            3   
18585      4                 5    81               93            3   
20537      5                 5    63               83            3   
20538      5                 5    63               93            3   
20618      5                 5    83               93            3   
18583      4                 5    81               64            4   
3130       2                 5    89               83            4   
12395      3                 3    25               64            3   
13879      3                 4    64               87            3   
9050       2     

In [13]:
data_frame_distinct = data_frame.drop_duplicates(subset='lcs', keep='first', inplace=False)
data_frame_distinct

surat  surat_pembanding  ayat  ayat_pembanding  jumlah_kata  \
0          1                 1     1                3            5   
1          1                 2     1               37            3   
3          1                 2     1              114            3   
7          1                 2     1              163            6   
16         1                 3     1              126            3   
33         1                 2     2              131            3   
64         1                 2     5               41            3   
70         1                 2     6              108            3   
82         1                 2     7               32            3   
83         1                 2     7               73            3   
92         1                 3     7               67            3   
102        2                 3     1                1            3   
103        2                 2     2                4            3   
104        2                 2     2               66            3   
106        2                 3     2               25            3   
109        2                 3     2                9            3   
110        2                 3     2              138            3   
112        2                 2     3                4            4   
113        2                 2     3               25            3   
115        2                 2     3              177            3   
116        2                 2     3              213            3   
121        2                 4     3               39            5   
122        2                 4     3              150            3   
124        2                 4     3              162            3   
127        2                 5     3               55            4   
128        2                 2     4               23            3   
132        2                 2     4               90            3   
147        2                 4     4               60            3   
149        2                 4     4              162            4   
153        2                 5     4               83            4   
...      ...               ...   ...              ...          ...   
20422      5                 5    52               71            5   
20438      5                 5    53              107            3   
20457      5                 5    55               56            6   
20478      5                 5    57               58            4   
20498      5                 5    57              112            6   
20503      5                 5    59               64            3   
20530      5                 5    62               63            5   
20531      5                 5    62               68            3   
20534      5                 5    62               80            4   
20541      5                 5    64               66            5   
20542      5                 5    64               67            5   
20543      5                 5    64               68            8   
20544      5                 5    64               73            3   
20547      5                 5    64               91            5   
20551      5                 5    66               68            6   
20553      5                 5    66              110            4   
20578      5                 5    72               75            4   
20580      5                 5    72              117            5   
20583      5                 5    73              110            3   
20599      5                 5    79               80            5   
20641      5                 5    90               94            5   
20643      5                 5    90               97            3   
20644      5                 5    90              100            4   
20650      5                 5    92               98            3   
20665      5                 5    95              106            7   
20671      5     

In [14]:
data_frame_distinct.drop(['surat', 'surat_pembanding', 'ayat', 'ayat_pembanding'], axis=1, inplace=True)

C:\Users\DEVI\Anaconda3\lib\site-packages\pandas\core\frame.py:3697: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


In [15]:
def join_verses_for_lcs(lcs: str):
    matches = data_frame.loc[data_frame['lcs'] == lcs]
    verses1 = matches.apply(lambda row: '%s:%s' % (row['surat'], row['ayat']), axis=1)
    verses2 = matches.apply(lambda row: '%s:%s' % (row['surat_pembanding'], row['ayat_pembanding']), axis=1)
    verseset = list(verses1) + list(verses2) # concatenate lists
    verseset = list(dict.fromkeys(verseset)) # remove duplicate verses
    return verseset

# join_verses_for_lcs('yang kami')
data_frame_distinct = data_frame_distinct.copy()
data_frame_distinct['first_verse'] = data_frame_distinct.apply(lambda row: join_verses_for_lcs(row['lcs'])[0], axis=1)
data_frame_distinct['verses'] = data_frame_distinct.apply(lambda row: ', '.join(join_verses_for_lcs(row['lcs'])), axis=1)
data_frame_distinct['verse_count'] = data_frame_distinct.apply(lambda row: len(join_verses_for_lcs(row['lcs'])), axis=1)
data_frame_distinct

jumlah_kata                                                lcs  \
0                5                   maha pemurah lagi maha penyayang   
1                3                                lagi maha penyayang   
3                3                                menyebut nama allah   
7                6              yang maha pemurah lagi maha penyayang   
16               3                                    allah yang maha   
33               3                                 tuhan semesta alam   
64               3                                   dan hanya kepada   
70               3                                   jalan yang lurus   
82               3                                  yang telah engkau   
83               3                             orang-orang yang telah   
92               3                                     dan bukan pula   
102              3                                     alif laam miim   
103              3                                     kitab al quran   
104              3                                   bagi mereka yang   
106              3                                 tidak ada keraguan   
109              3                               ada keraguan padanya   
110              3                                       al quran ini   
112              4                         mereka yang beriman kepada   
113              3                                mereka yang beriman   
115              3                              mendirikan shalat dan   
116              3                                yang beriman kepada   
121              5             dan menafkahkan sebahagian rezeki yang   
122              3                                beriman kepada yang   
124              3                             yang mendirikan shalat   
127              4                         yang mendirikan shalat dan   
128              3                                      al quran yang   
132              3                              yang telah diturunkan   
147              3                            diturunkan kepadamu dan   
149              4                    yang telah diturunkan sebelummu   
153              4                                al quran yang telah   
...            ...                                                ...   
20422            5                     maka karena itu mereka menjadi   
20438            3                                  dengan nama allah   
20457            6       allah rasul-nya dan orang-orang yang beriman   
20478            4                          buah ejekan dan permainan   
20498            6     bertakwalah kepada allah jika kamu betul-betul   
20503            3                               kebanyakan di antara   
20530            5                   sesungguhnya amat buruk apa yang   
20531            3                             kebanyakan dari mereka   
20534            4                     melihat kebanyakan dari mereka   
20541            5                       dan al quran yang diturunkan   
20542            5              yang diturunkan kepadamu dari tuhanmu   
20543            8  dan al quran yang diturunkan kepadamu dari tuh...   
20544            3                                 mereka katakan itu   
20547            5                 permusuhan dan kebencian di antara   
20551            6                 injil dan al quran yang diturunkan   
20553            4                               taurat dan injil dan   
20578            4                             al masih putera maryam   
20580            5                sembahlah allah tuhanku dan tuhanmu   
20583            3                              kafir diantara mereka   
20599            5                sesungguhnya amat buruklah apa yang   
20641            5          hai orang-orang yang beriman sesungguhnya   
20643            3                                      itu agar kamu   
20644            4                   agar kamu mendapat keberuntu

In [16]:
from pandas import ExcelWriter

writer = ExcelWriter('data_surat1-5_indo.xlsx')
data_frame_distinct.to_excel(writer,'indo')
writer.save()

In [29]:
# !pip install lang-trans

In [11]:
# from lang_trans.arabic import buckwalter

In [30]:
# print buckwalter.untransliterate('bi somi {ll~ahi {l r~aHoma`ni {l r~aHiymi')

In [31]:
# !pip install translation

In [32]:
# from translation import google, ConnectError

# # 127.0.0.1:1080 is a vaild proxies
# try:
#     print(google('hello world!', dst = 'zh-CN', proxies = {'http': '127.0.0.1:1080'}))
# except ConnectError:
#     print('Invaild proxy')